This is the notebook for designing semiconductor heterostructures based on Materials Project data.

In [1]:
import numpy as np
import copy
import scipy.constants as cons
import os
import bisect
import re
import itertools
#from sklearn import svm
#from sklearn.model_selection import cross_validate as cross_validation
from shutil import copyfile
import collections
import random
import sys

The next section performs preprocessing of data.

In [2]:
def CostFunction(CostName):
    CostVal=0.0
    ENegC=[]
    for k in range(0,len(CostName),2):
        ElementIndex=Elements.index(CostName[k])
        CostVal+=float(CostName[k+1])/Abundances[ElementIndex]
        
        OrderedElementIndex=OrderedElements.index(CostName[k])
        ENegC.append(Electronegativity[OrderedElementIndex])
    ENegDif=max(ENegC)-min(ENegC)
        
    return CostVal,ENegDif

MaterialAbundances=np.genfromtxt('Abundances.txt',dtype=None)
ENegData=np.genfromtxt('Electronegativity.txt',dtype=None)
Elements=[]
Abundances=[]
OrderedElements=[]
Electronegativity=[]
for i in range(0,len(MaterialAbundances)):
    Elements.append(MaterialAbundances[i][0].decode("utf-8"))
    Abundances.append(float(MaterialAbundances[i][1]))
for i in range(0,len(ENegData)):
    OrderedElements.append(ENegData[i][0].decode("utf-8"))
    Electronegativity.append(ENegData[i][1])

MaterialNames=np.genfromtxt('ChemComps.txt',dtype=None)
filename3='ChemicalCompositions.txt'
h=open(filename3,'w')
h.write('#MP_Number'+'\t'+'Formula'+'\t'+'Cost'+'\t'+'ENegDiff'+'\t'+'Separated_Formula'+'\n')

IDs=[]
Names=[]
for i in range(0,len(MaterialNames)):
    IDs.append(MaterialNames[i][0])
    Names.append(MaterialNames[i][1].decode("utf-8"))

for i in range(0,len(Names)):
    #print IDs[i],Names[i]
    NameToTest=Names[i]
    NameToTest= [ y for y in list(itertools.chain(*[re.split(r'\"(.*)\"', x) 
        for x in re.split(r'\((.*)\)', NameToTest)])) 
        if y != ''] #this splits at parenthases
    ParenSeparatedName=[]
    for j in range(0,len(NameToTest)):#This will check if first character is a number, due to parenthases
        firstChar=NameToTest[j][0]
        if firstChar.isdigit()==True:
            ParenSeparatedName.extend([a for a in re.split(r'([A-Z][a-z]*\d*)', NameToTest[j]) if a])
        else:
            #print NameToTest[j]
            ParenSeparatedName.append(NameToTest[j])
    #print ParenSeparatedName    
    SeparatedName=[]
    for j in range(0,len(ParenSeparatedName)):
        TempSegment=[a for a in re.split(r'([A-Z][a-z]*)', ParenSeparatedName[j]) if a]
        #print TempSegment
        multiplier=1
        if TempSegment[0].isdigit()==False:
            if j<len(ParenSeparatedName)-1 and ParenSeparatedName[j+1].isdigit()==True:
                multiplier=int(ParenSeparatedName[j+1])
            #print multiplier #from parenthases
            for k in range(0,len(TempSegment)):
                #print TempSegment[k]
                if TempSegment[k].isdigit()==False:
                    if k<len(TempSegment)-1 and TempSegment[k+1].isdigit()==True:
                        SeparatedName.append(TempSegment[k])
                        SeparatedName.append(str(int(TempSegment[k+1])*multiplier))
                    elif k<len(TempSegment)-1 and TempSegment[k+1].isdigit()==False:
                        SeparatedName.append(TempSegment[k])
                        SeparatedName.append(str(multiplier))
                    elif k==len(TempSegment)-1 and TempSegment[k].isdigit()==False:
                        SeparatedName.append(TempSegment[k])
                        SeparatedName.append(str(multiplier))
    
    #now calculate cost
    NewCost,ENegDiff2=CostFunction(SeparatedName)
    
    dataToWrite=[int(IDs[i]),Names[i],NewCost,ENegDiff2]+SeparatedName
    for item in dataToWrite:
        h.write("%s\t" % item)
    h.write('\n')

h.close()
print('Done')

<ipython-input-2-44ecc04cbb8b>:13: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  MaterialAbundances=np.genfromtxt('Abundances.txt',dtype=None)
<ipython-input-2-44ecc04cbb8b>:14: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  ENegData=np.genfromtxt('Electronegativity.txt',dtype=None)
<ipython-input-2-44ecc04cbb8b>:29: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  MaterialNames=np.genfromtxt('ChemComps.txt',dtype=None)


Done


The next cell defines metal versus semiconductor in terms of the band gap.  It allows for semiconductors which have small negative gaps within DFT.  The value provided here assumes that the gap has already been corrected.  The provided value assumes a linear gap correction from Setyawan $\textit{et. al. }$ (DOI:10.1021/co200012w)

In [3]:
MinSemicondGap=-0.677

The folowing cell provides an initial filtering to remove metals.  

In [4]:
#import data from file
MaterialDataHold=np.genfromtxt('CNData.txt',dtype=None) #input bandstruct data from MP
#file to write filtered data
filename2='CNData_Semicond.txt'
g=open(filename2,'w')
g.write('#MP_Number'+'\t'+'CNL'+'\t'+'EG'+'\t'+'EFermi'+'\t'+'ValenceMax'+'\t'+'CondMin'+'\n')

for i in range(0,len(MaterialDataHold)): #here will get densities, EHull from materials project  
    if (MaterialDataHold[i][2]>MinSemicondGap):
        for item in MaterialDataHold[i]:
            g.write("%s\t" % item)
        g.write('\n')
            
g.close()
print('Done')

<ipython-input-4-b0e3d091dc3f>:2: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  MaterialDataHold=np.genfromtxt('CNData.txt',dtype=None) #input bandstruct data from MP


Done


The next cell provides the settings for the first layer of filtering.  Specify the ranges of:

-Density in g/cm$^3$

-Energy above the convex hull in eV

-Number of atoms in the unit cell

In [5]:
densityMin=2.0
densityMax=100.0 #min and max densities

eHullMin=0.0
eHullMax=0.01

NumAtomMin=0 #minimum number of atoms per unit cell
NumAtomMax=45 #maximum number of atoms per unit cell

The next cell provides settings for the second filter.  Specify:

-Elements to exclude

-Materials to exclude by MPID

-Range of allowed Pauling electronegativity differences

-Range of number of allowed elements in the formula.

In [6]:
#Elements to exclude:
ExcludeElems=['H','He','Ne','Ar','Kr','Xe','Rn','Li','Be','Tc','Hg','Tl','Rh','Re','Os',
              'Ce','Pr','Nd','Pm','Sm','Eu','Gd','Tb','Dy','Ho','Er','Tm','Yb','Lu',
              'Ac','Th','Pa','U','Np','Pu']
#ExcludeElems=[]
#MPIDs to exclude, as integer
ExcludeIDs=[]#361,713,1342,2072,1266,8755,2784,2400,555214,3257,5367]

ENegDiffMin=0.0 #minimum difference in electronegativity between most and least electronegative elements
ENegDiffMax=2.5 #1.24 #maximum allowed ENeg difference 1.24 for O-H, 1.78 for HF, 0.79 for CH3NH3PbI3

NumElementsMin=0 #minimum number of elements per compound
NumElementsMax=3 #maximum number of elements allowed in material

The next cell applies the filters.

In [7]:
#import data from file
MaterialDataHold=np.genfromtxt('CNData_Semicond.txt',dtype=None) 
Descriptors=np.genfromtxt('Descriptors.txt',dtype=None) #input physical data
AllIDs=[] #all of these have same indexing
AllNames=[]
ENegDiffs=[]
AllPrettyFormulas=[]
AllCosts=[]
with open('ChemicalCompositions.txt') as f: #lines are unequal length
    next(f) #skip header
    for line in f:
        AllIDs.append(int(line.split('\t')[0]))
        AllPrettyFormulas.append(line.split('\t')[1])
        AllNames.append(line.split('\t')[4:-1]) #names separated by element with numbers, example:['S', '1']
        ENegDiffs.append(float(line.split('\t')[3]))
        AllCosts.append(float(line.split('\t')[2]))

filename3='CNData_DensityEHullNAt_CompENeg.txt'
h=open(filename3,'w')
h.write('#MP_Number'+'\t'+'CNL'+'\t'+'EG'+'\t'+'EFermi'+'\t'+'ValenceMax'+'\t'+'CondMin'+'\t'+'ENegDiff'+'\t'+'Formula'+'\t'+'Cost'+'\n')
for i in range(0,len(MaterialDataHold)):
    #find separated name for ith compound in datalist
    NameIndex=AllIDs.index(MaterialDataHold[i][0]) #finds where ith compound in CNL data is in chemical comp
    SeparatedName=AllNames[NameIndex] #separated name of ith compound in CNL data
    ENegDiff=ENegDiffs[NameIndex]
    Formula=AllPrettyFormulas[NameIndex]
    Cost=AllCosts[NameIndex]
    Density=Descriptors[NameIndex][1]
    eHull=Descriptors[NameIndex][2]
    NAtom=Descriptors[NameIndex][9]
    #filter by density, eHull, NAtom
    if (    densityMin<=Density<=densityMax
        and eHullMin<=eHull<=eHullMax
        and NumAtomMin<=NAtom<=NumAtomMax
        ):
        #filter by elements
        if (    set(SeparatedName).isdisjoint(set(ExcludeElems))==True
            and 2*NumElementsMin<=len(SeparatedName)<=2*NumElementsMax
            and ENegDiffMin<=ENegDiff<=ENegDiffMax
            ): 
            if MaterialDataHold[i][0] in ExcludeIDs:
                continue
            else:
                for item in list(MaterialDataHold[i])+[ENegDiff,Formula,Cost]:
                    h.write("%s\t" % item)
                h.write('\n')         
h.close()
print('Done')

<ipython-input-7-81ebc8bc16ad>:2: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  MaterialDataHold=np.genfromtxt('CNData_Semicond.txt',dtype=None)


Done


The following cell specifies the method of correcting the band gap.  Provided here is a two-tiered approach.  The first choice is that the user provides a datafile with lists of experimental band gap values.  The second is an analytic equation based on a best fit linear correction two fitting parameters from literature.

In [8]:
def GapCorrection(OriginalGap): #user defined function for gap correction
    NewGap=SlopeCorrection*OriginalGap+InterceptCorrection #This is Curtarolo Correction
    return NewGap

SlopeCorrection=1.348#Curtarolo     #1.242 #Self
InterceptCorrection=0.913#Curtarolo     #0.974#Self

ExpData=np.genfromtxt('ExperimentalGaps.csv',dtype=None,delimiter=',') #experimentally known gaps


The next cell applies the gap correction scheme.

In [9]:
CNLData=np.genfromtxt('CNData_DensityEHullNAt_CompENeg.txt',dtype=None)
UserData=[]
try:
    UserData=np.genfromtxt('UserData.txt',dtype=None) #User provided data
except (TypeError):
    pass
    
ExpIDs=[]
ExpGaps=[]
for i in range(0,len(ExpData)):
    ExpIDs.append(ExpData[i][0])
    ExpGaps.append(ExpData[i][1])

CNLDataCorrected=copy.deepcopy(CNLData) #This will hold data with corrected band gap, change element by element
for i in range(0,len(CNLDataCorrected)):
    OldGap=CNLData[i][2]
    #find Corrected Gap
    
    if CNLData[i][0] in ExpIDs:
        CorrectGap=ExpGaps[ExpIDs.index(CNLData[i][0])]
    else:
        CorrectGap=GapCorrection(CNLData[i][2])
    
    GapShift=CorrectGap-OldGap #how much gap is corrected, will change CNL and CBM

    CNLDataCorrected[i][1]+=GapShift/2
    CNLDataCorrected[i][2]=CorrectGap
    CNLDataCorrected[i][5]+=GapShift
       
CNLDataCorrectedCNL0=copy.deepcopy(CNLDataCorrected)
for i in range(0,len(CNLDataCorrected)):
    CNL=CNLDataCorrected[i][1]
        #Now set CNL to 0 eV
    CNLDataCorrectedCNL0[i][3]-=CNL+CNLDataCorrected[i][4]
    CNLDataCorrectedCNL0[i][4]-=CNL+CNLDataCorrected[i][4]
    CNLDataCorrectedCNL0[i][5]-=CNL+CNLDataCorrected[i][4]

UserDataList=copy.deepcopy(UserData)
for i in range(0,len(UserData)): #This will take user data, set CNL=0
    UserDataList[i][3]-=UserData[i][1]+UserData[i][4]
    UserDataList[i][4]-=UserData[i][1]+UserData[i][4]
    UserDataList[i][5]-=UserData[i][1]+UserData[i][4]

filename='CNData_DensityEHullNAt_CompENeg_GapCorr.txt'
f=open(filename,'w')  
f.write('#MP_Number'+'\t'+'CNL'+'\t'+'EG'+'\t'+'EFermi'+'\t'+'ValenceMax'+'\t'+'CondMin'+'\t'+'ENegDiff'+'\t'+'Formula'+'\t'+'Cost'+'\n')
f.writelines('\t'.join(str(j) for j in i) + '\n' for i in CNLDataCorrected)
f.close()

filename1='CNData_DensityEHullNAt_CompENeg_GapCorrCNL0.txt'
g=open(filename1,'w')  
g.write('#MP_Number'+'\t'+'CNL'+'\t'+'EG'+'\t'+'EFermi'+'\t'+'ValenceMax'+'\t'+'CondMin'+'\t'+'ENegDiff'+'\t'+'Formula'+'\t'+'Cost'+'\n')
g.writelines('\t'.join(str(j) for j in i) + '\n' for i in CNLDataCorrectedCNL0)
g.writelines('\t'.join(str(j) for j in i) + '\n' for i in UserDataList)
g.close()
print('Done')

<ipython-input-9-198f53083f88>:1: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  CNLData=np.genfromtxt('CNData_DensityEHullNAt_CompENeg.txt',dtype=None)
<ipython-input-9-198f53083f88>:4: UserWarning: genfromtxt: Empty input file: "UserData.txt"
  UserData=np.genfromtxt('UserData.txt',dtype=None) #User provided data


Done


The following cell specifies materials to make into nanocrystals.  The format is (MPID, radius in nm).

In [10]:
#format is (mpid,radii in nm)
QuantumDots=[(21276,5)]

The below cell constructs the nanocrystals and appends to existing datafiles.

In [11]:
def QDotID(mpid,rad): #new mpid based on material and radius
    newid=10**8*mpid+rad*10**2
    return newid

def gapShift(rad,meEff,mhEff):
    shift=h**2/(8*(rad*10**-9)**2*me)*(1/meEff+1/mhEff)*eV
    return shift

me=cons.electron_mass
h=cons.h
eV=6.241509126*10**18

ElectronicData=np.genfromtxt('CNData_DensityEHullNAt_CompENeg_GapCorrCNL0.txt',dtype=None) #This includes the gap correction
OpticalData=np.genfromtxt('OpticalProperties.txt',dtype=None)
OpticIDs=[]
for i in range(0,len(OpticalData)):
    OpticIDs.append(OpticalData[i][0])
ElectronicIDs=[]
for i in range(0,len(ElectronicData)):
    ElectronicIDs.append(ElectronicData[i][0])
Descriptors=np.genfromtxt('Descriptors.txt',dtype=None)
Comps=np.genfromtxt('ChemComps.txt',dtype=None)
#Specify files to be appended
ElectronicFile=open('CNData_DensityEHullNAt_CompENeg_GapCorrCNL0.txt','a')  
OpticsFile=open('OpticalProperties.txt','a')
DescriptorFile=open('Descriptors.txt','a')
NameFile=open('ChemicalCompositions.txt','a')
NameFile2=open('ChemComps.txt','a')
    
for i in range(0,len(QuantumDots)):
    FilteredIndex=ElectronicIDs.index(QuantumDots[i][0]) #for electronic data
    UnfilteredIndex=OpticIDs.index(QuantumDots[i][0])
    mEl=OpticalData[UnfilteredIndex][2]
    mHole=OpticalData[UnfilteredIndex][3]
    
    with open('ChemicalCompositions.txt') as CC:
        for j, line in enumerate(CC):
            if j==UnfilteredIndex+1:
                NameLin=line.split()
            elif j>UnfilteredIndex+1:
                break
    #print NameLin
    for whichRad in range(1,len(QuantumDots[i])):
        NewID=QDotID(QuantumDots[i][0], QuantumDots[i][whichRad])
        GapShift=gapShift(QuantumDots[i][whichRad],mEl,mHole)
        #print GapShift
        ElectronicLine=copy.copy(ElectronicData[FilteredIndex])
        ElectronicLine[0]=int(NewID)
        ElectronicLine[1]+=GapShift/2 #CNL
        ElectronicLine[2]+=GapShift #EG
        ElectronicLine[3]+=-GapShift/2 #EF
        ElectronicLine[4]+=-GapShift/2 #VBM rel to CNL
        ElectronicLine[5]+=GapShift/2 #CBM rel to CNL
        ElectronicFile.writelines(["%s\t" % item  for item in ElectronicLine])
        ElectronicFile.write('\n')
        #Now add line to OpticsFile
        OpticsLine=copy.copy(OpticalData[UnfilteredIndex])
        OpticsLine[0]=int(NewID)
        OpticsFile.writelines(["%s\t" % item  for item in OpticsLine])
        OpticsFile.write('\n')
        #Now add line to Descriptor file
        DescriptorLine=copy.copy(Descriptors[UnfilteredIndex])
        DescriptorLine[0]=int(NewID)
        DescriptorFile.writelines(["%s\t" % item  for item in DescriptorLine])
        DescriptorFile.write('\n')
        #Now add line to ChemicalCompositions file
        NameLine=copy.copy(NameLin)
        NameLine[0]=int(NewID)
        NameFile.writelines(["%s\t" % item  for item in NameLine])
        NameFile.write('\n')
        #Add line to ChemComps file
        CompsLine=copy.copy(Comps[UnfilteredIndex])
        CompsLine[0]=int(NewID)
        NameFile2.writelines(["%s\t" % item  for item in CompsLine])
        NameFile2.write('\n')
ElectronicFile.close()
OpticsFile.close()
DescriptorFile.close()
NameFile.close()
NameFile2.close()
print('Done')

<ipython-input-11-4d5225591bcd>:13: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  ElectronicData=np.genfromtxt('CNData_DensityEHullNAt_CompENeg_GapCorrCNL0.txt',dtype=None) #This includes the gap correction


Done


<ipython-input-11-4d5225591bcd>:22: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  Comps=np.genfromtxt('ChemComps.txt',dtype=None)


The next cell are the parameters used for constructing heterostructures.

In [12]:
iterations=1 #number of iterations through main loop

Lefts=[0]
#2691 - CdSe
#20351 - InP
#100000000,100000001,100000002 - MAPbI3
#2127600000500 PbS nanocrystal
# Middles=[1000000000] #put [0] for all possible
Middles=[2691]
Rights=[0] 
#361 - Cu2O
Layers=[]#['Left','Right']#['Left','Right']#['Left']#['Left','Right'] #Which layers for which to use SVM, empty for no S4VM
AllLayers=['Left','Middle','Right'] #Leave this alone
AllBad=[23204,21892,634859,1968,2858,2310,2156,1170,985829,602]
LeftTrainingInitialGood=[554278,2858,5909,2133,856,20411] #ETL
LeftTrainingInitialBad=[18856,19443,25620,715434,18748,361]+AllBad
MiddleTrainingInitialGood=[]
MiddleTrainingInitialBad=[]
RightTrainingInitialGood=[18856,19443,25620,715434,18748,361] #HTL 
RightTrainingInitialBad=[554278,2858,5909,2133,856,20411]+AllBad
SVMAppendFrac=0.1 #fraction of most common materials to add to SVM training set
SVM_C=2.0 #SVM hinge function
SVMIterations=1000000 #maximum number of iterations for individual SVM
NewSVMPoints=10 #number of points to add to data set in S4VM
PointCombinations=500 #number of combinations of new points to add to training set
MaxS4VM=10 #Maximum number of S4VM loops in case of no convergence
SVM_Kernel='linear'
SlopeCorrection=1.348#Curtarolo     #1.242 #Self
InterceptCorrection=0.913#Curtarolo     #0.974#Self
S4VMChoice=1 #Method for choosing SVM surface,will maximize, 1->loss, 2->crossValidation, 3->cross/loss
CrossValidationNum=5
LeftExclude=0 #number of materials at end of data files to ignore
MiddleExclude=0
RightExclude=0

if 'Left' in Layers and(not LeftTrainingInitialGood or not LeftTrainingInitialBad):
    print ('Choose SVM training materials for Left component or turn off Left SVM')
    exit()
if 'Middle' in Layers and(not MiddleTrainingInitialGood or not MiddleTrainingInitialBad):
    print ('Choose SVM training materials for Middle component or turn off Middle SVM')
    exit()
if 'Right' in Layers and(not RightTrainingInitialGood or not RightTrainingInitialBad):
    print ('Choose SVM training materials for Right component or turn off Right SVM')
    exit()


#Here specify the minimum and maximum gaps allowed for each material.
#These are used only if materials are NOT selected (ie selected materials override gap range
LeftMinGap=0.0
LeftMaxGap=6.0
PhotoMinGap=0.8 #Minimum gap of photo layer
PhotoMaxGap=6.0 #Maximum gap of photo layer
RightMinGap=0.0
RightMaxGap=6.0

LeftRequireDirect='False'
RequireDirect='False' #does photolayer gap need to be direct?
RightRequireDirect='False'

# topDirectory='ZnSnN2-0208/'#'Heterostructures_CdSe-1NoSVM/'#'SVMVerification/Heterostructures_Cu2O-11.6/'
topDirectory='Heterostructures_CdSe-1NoSVM/'#'SVMVerification/Heterostructures_Cu2O-11.6/'
if not os.path.exists(topDirectory): #make directory
    os.makedirs(topDirectory)
else:
    sys.exit("Directory already Exists")
    

#offsets between left and center, CBM offsets max,min, VBM offsets max,min


LeftOffsets=[0.4,0.2,-0.2,-10.0] #LED
RightOffsets=[10.0,0.2,-0.2,-0.4]
#LeftOffsets=[-0.2,-0.8,-0.2,-0.8] #CH3NH3PbI3 solar cell
#RightOffsets=[0.8,0.2,0.8,0.2]


if LeftOffsets[0]<LeftOffsets[1] or LeftOffsets[2]<LeftOffsets[3]:
    print('Check Left offsets')
if RightOffsets[0]<RightOffsets[1] or RightOffsets[2]<RightOffsets[3]:
    print('Check Right offsets')
print('Done')

SystemExit: Directory already Exists

/opt/local/Library/Frameworks/Python.framework/Versions/3.8/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3445: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


The following cell constructs heterostructures.  This step may take minutes to hours depending on parameter choices.

In [13]:
def ChoosePhotolayers(Lefts,Middles,Rights,LeftMinGap,LeftMaxGap,PhotoMinGap,PhotoMaxGap,RightMinGap,RightMaxGap,LeftRequireDirect,RequireDirect,RightRequireDirect):
    if ((RequireDirect=='True' and Middles==[0]) or
        (LeftRequireDirect=='True' and Lefts==[0]) or
        (RightRequireDirect=='True' and Rights==[0])
        ): #require direct gap in middle and have free photolayer
        Descripts=np.genfromtxt('Descriptors.txt',dtype=None)
        DescIDs=[]
        DescDir=[]
        for i in range(0,len(Descripts)):
            DescIDs.append(Descripts[i][0])
            DescDir.append(Descripts[i][10])
    
    LeftData=[]
    if Lefts: #choose photolayers for LEDs
        if sorted(Lefts)!=[0]: 
            for i in range(0,len(AllData)):
                if AllData[i][0] in Lefts:
                    OpticIndex=OpticIDs.index(AllData[i][0])
                    OpticInfo=[OpticalData[OpticIndex][1],OpticalData[OpticIndex][2],OpticalData[OpticIndex][3],OpticalData[OpticIndex][4],OpticalData[OpticIndex][5]]
                    LeftData.append(list(AllData[i])+OpticInfo)
        else:
            for i in range(0,len(AllData)-LeftExclude):
                if  (   LeftMinGap<=AllData[i][2]<=LeftMaxGap):
                    if LeftRequireDirect=='True' and DescDir[DescIDs.index(AllData[i][0])]=='True': #Require direct gap
                        OpticIndex=OpticIDs.index(AllData[i][0])
                        OpticInfo=[OpticalData[OpticIndex][1],OpticalData[OpticIndex][2],OpticalData[OpticIndex][3],OpticalData[OpticIndex][4],OpticalData[OpticIndex][5]]
                        LeftData.append(list(AllData[i])+OpticInfo)
                    elif LeftRequireDirect=='False': #do not require direct gap
                        OpticIndex=OpticIDs.index(AllData[i][0])
                        OpticInfo=[OpticalData[OpticIndex][1],OpticalData[OpticIndex][2],OpticalData[OpticIndex][3],OpticalData[OpticIndex][4],OpticalData[OpticIndex][5]]
                        LeftData.append(list(AllData[i])+OpticInfo)
    
    MiddleData=[]
    if Middles: #choose photolayers for LEDs
        if sorted(Middles)!=[0]: 
            for i in range(0,len(AllData)):
                if AllData[i][0] in Middles:
                    OpticIndex=OpticIDs.index(AllData[i][0])
                    OpticInfo=[OpticalData[OpticIndex][1],OpticalData[OpticIndex][2],OpticalData[OpticIndex][3],OpticalData[OpticIndex][4],OpticalData[OpticIndex][5]]
                    MiddleData.append(list(AllData[i])+OpticInfo)
        else:
            for i in range(0,len(AllData)-MiddleExclude):
                if  (   PhotoMinGap<=AllData[i][2]<=PhotoMaxGap):
                    if RequireDirect=='True' and DescDir[DescIDs.index(AllData[i][0])]=='True': #Require direct gap
                        OpticIndex=OpticIDs.index(AllData[i][0])
                        OpticInfo=[OpticalData[OpticIndex][1],OpticalData[OpticIndex][2],OpticalData[OpticIndex][3],OpticalData[OpticIndex][4],OpticalData[OpticIndex][5]]
                        MiddleData.append(list(AllData[i])+OpticInfo)
                    elif RequireDirect=='False': #do not require direct gap
                        OpticIndex=OpticIDs.index(AllData[i][0])
                        OpticInfo=[OpticalData[OpticIndex][1],OpticalData[OpticIndex][2],OpticalData[OpticIndex][3],OpticalData[OpticIndex][4],OpticalData[OpticIndex][5]]
                        MiddleData.append(list(AllData[i])+OpticInfo)
    
    RightData=[]
    if Rights: #choose photolayers for LEDs
        if sorted(Rights)!=[0]: 
            for i in range(0,len(AllData)):
                if AllData[i][0] in Rights:
                    OpticIndex=OpticIDs.index(AllData[i][0])
                    OpticInfo=[OpticalData[OpticIndex][1],OpticalData[OpticIndex][2],OpticalData[OpticIndex][3],OpticalData[OpticIndex][4],OpticalData[OpticIndex][5]]
                    RightData.append(list(AllData[i])+OpticInfo)
        else:
            for i in range(0,len(AllData)-RightExclude):
                if  (   RightMinGap<=AllData[i][2]<=RightMaxGap):
                    if RightRequireDirect=='True' and DescDir[DescIDs.index(AllData[i][0])]=='True': #Require direct gap
                        OpticIndex=OpticIDs.index(AllData[i][0])
                        OpticInfo=[OpticalData[OpticIndex][1],OpticalData[OpticIndex][2],OpticalData[OpticIndex][3],OpticalData[OpticIndex][4],OpticalData[OpticIndex][5]]
                        RightData.append(list(AllData[i])+OpticInfo)
                    elif RightRequireDirect=='False': #do not require direct gap
                        OpticIndex=OpticIDs.index(AllData[i][0])
                        OpticInfo=[OpticalData[OpticIndex][1],OpticalData[OpticIndex][2],OpticalData[OpticIndex][3],OpticalData[OpticIndex][4],OpticalData[OpticIndex][5]]
                        RightData.append(list(AllData[i])+OpticInfo)
    
    
    #if MiddleData: #checks if any LEDs desired
    filename=topDirectory+'HeterostructureLeft.txt'
    f=open(filename,'w')  
    f.write('#MP_Number'+'\t'+'CNL'+'\t'+'EG'+'\t'+'EFermi'+'\t'+'ValenceMax'+'\t'+'CondMin'+'\t'+'ENegDiff'+'\t'+'Formula'+'\t'+'Cost'+'\t'+'Eps10'+'\t'+'MeffEl'+'\t'+'MeffHole'+'\t'+'Exciton'+'\t'+'JDOSEdge'+'\n')
    f.writelines('\t'.join(str(j) for j in i) + '\n' for i in LeftData)
    f.close()
    if not LeftData:
        print('No Valid Left Layers Found')
    filename=topDirectory+'HeterostructureMiddle.txt'
    f=open(filename,'w')  
    f.write('#MP_Number'+'\t'+'CNL'+'\t'+'EG'+'\t'+'EFermi'+'\t'+'ValenceMax'+'\t'+'CondMin'+'\t'+'ENegDiff'+'\t'+'Formula'+'\t'+'Cost'+'\t'+'Eps10'+'\t'+'MeffEl'+'\t'+'MeffHole'+'\t'+'Exciton'+'\t'+'JDOSEdge'+'\n')
    f.writelines('\t'.join(str(j) for j in i) + '\n' for i in MiddleData)
    f.close()
    if not MiddleData:
        print('No Valid Photo Layers Found')
    filename=topDirectory+'HeterostructureRight.txt'
    f=open(filename,'w')  
    f.write('#MP_Number'+'\t'+'CNL'+'\t'+'EG'+'\t'+'EFermi'+'\t'+'ValenceMax'+'\t'+'CondMin'+'\t'+'ENegDiff'+'\t'+'Formula'+'\t'+'Cost'+'\t'+'Eps10'+'\t'+'MeffEl'+'\t'+'MeffHole'+'\t'+'Exciton'+'\t'+'JDOSEdge'+'\n')
    f.writelines('\t'.join(str(j) for j in i) + '\n' for i in RightData)
    f.close()
    if not RightData:
        print('No Valid Right Layers Found')
    return


def HingeLoss(BoundParams,Intercept,Descriptors,Classes): #Hinge loss function for finding best choice of SVM
    values=[]
    for qq in range(0,len(Classes)):
        val=1-Classes[qq]*(np.dot(BoundParams,Descriptors[qq])+Intercept)
        if val>0:
            values.append(val)
        else:
            values.append(0)
    loss=np.mean(values)+SVM_C*np.dot(BoundParams,BoundParams)
    
    return loss


def SVMMaterial(iteration,LayerToStudy):
    goodLayer=np.atleast_1d(np.genfromtxt(directory+'SVMTraining'+'Iteration'+str(iteration)+'Good'+LayerToStudy+'.txt'))
    badLayer=np.atleast_1d(np.genfromtxt(directory+'SVMTraining'+'Iteration'+str(iteration)+'Bad'+LayerToStudy+'.txt'))
    
    ElectronicData=AllData
    FullElectronicData=np.genfromtxt('CNData.txt',dtype=None) #will be used for training set only, same indexing as Descriptors
    Descriptors=np.genfromtxt('Descriptors.txt',dtype=None)
    ENegDiffs=[]
    with open('ChemicalCompositions.txt') as f: #lines are unequal length
        next(f) #skip header
        for line in f:
            ENegDiffs.append(float(line.split('\t')[3]))
    #IDList=[]
    #for i in range(0,len(ElectronicData)):
    #    IDList.append(Descriptors[i][0])
    IDList=OpticIDs
    ElectronicIDList=ElectronicIDs
    
    #Here assemble matrix of descriptors
    LayersData=np.genfromtxt(topDirectory+'Heterostructure'+LayerToStudy+'.txt',dtype=None)
    numMats=len(LayersData)
    MaterialDescriptorMatrix=[[]]*numMats
    FilteredIDs=[]
    for i in range(0,numMats): #This sets up matrix with all post filtered materials
        #find location of valid material in unfiltered lists
        materialIndex=IDList.index(LayersData[i][0]) #index in unfiltered list
        electronicIndex=ElectronicIDList.index(LayersData[i][0])
        FilteredIDs.append(LayersData[i][0]) #ids of materials in allowed list
        ECNL=ElectronicData[electronicIndex][1]
        EG=ElectronicData[electronicIndex][2]
        Eps10=OpticalData[materialIndex][1]
        eMass=OpticalData[materialIndex][2]
        hMass=OpticalData[materialIndex][3]
        excitonBinding=OpticalData[materialIndex][4]
        EdgeJDOS=OpticalData[materialIndex][5]
        ENegDiff=ENegDiffs[materialIndex]
        if Descriptors[materialIndex][10]=='True':
            direct=1.0 #direct band gap
        else:
            direct=-1.0 #inderect band gap
        
        if LayerToStudy!='Middle': #Transport Layer
            MaterialDescriptors=[ECNL/EG, EG, Eps10, eMass, hMass,EdgeJDOS,ENegDiff]
        else: #Photolayer
            MaterialDescriptors=[ECNL/EG, EG, Eps10,excitonBinding,EdgeJDOS,ENegDiff]
        MaterialDescriptorMatrix[i]=MaterialDescriptors
    #Set up initial training set and SVM
    InitialTrainingDesc=[[]]*(len(goodLayer)+len(badLayer))
    InitialTrainingClasses=[1]*len(goodLayer)+[-1]*len(badLayer)
    for i in range(0,len(goodLayer)): #This will use unfiltered material list
        layerIndex=IDList.index(int(goodLayer[i])) #location in unfiltered
        elecIndex=layerIndex#ElectronicIDList.index(int(goodLayer[i]))
        ECNL=FullElectronicData[elecIndex][1]+(FullElectronicData[elecIndex][2]*(SlopeCorrection-1)+InterceptCorrection)/2
        EG=FullElectronicData[elecIndex][2]*SlopeCorrection+InterceptCorrection
        Eps10=OpticalData[layerIndex][1]
        eMass=OpticalData[layerIndex][2]
        hMass=OpticalData[layerIndex][3]
        excitonBinding=OpticalData[layerIndex][4]
        EdgeJDOS=OpticalData[layerIndex][5]
        ENegDiff=ENegDiffs[layerIndex]
        if Descriptors[layerIndex][10]=='True':
            direct=1.0 #direct band gap
        else:
            direct=-1.0 #inderect band gap
        
        if LayerToStudy!='Middle': #Transport Layer
            MaterialDescriptors=[ECNL/EG, EG, Eps10, eMass, hMass,EdgeJDOS,ENegDiff]
        else: #Photolayer
            MaterialDescriptors=[ECNL/EG, EG, Eps10,excitonBinding,EdgeJDOS,ENegDiff]
        InitialTrainingDesc[i]=MaterialDescriptors
    for i in range(0,len(badLayer)): #This will use unfiltered material list
        layerIndex=IDList.index(int(badLayer[i])) #location in unfiltered
        elecIndex=layerIndex#ElectronicIDList.index(int(badLayer[i]))
        ECNL=FullElectronicData[elecIndex][1]+(FullElectronicData[elecIndex][2]*(SlopeCorrection-1)+InterceptCorrection)/2
        EG=FullElectronicData[elecIndex][2]*SlopeCorrection+InterceptCorrection
        Eps10=OpticalData[layerIndex][1]
        eMass=OpticalData[layerIndex][2]
        hMass=OpticalData[layerIndex][3]
        excitonBinding=OpticalData[layerIndex][4]
        EdgeJDOS=OpticalData[layerIndex][5]
        ENegDiff=ENegDiffs[layerIndex]
        if Descriptors[layerIndex][10]=='True':
            direct=1.0 #direct band gap
        else:
            direct=-1.0 #inderect band gap
        
        if LayerToStudy!='Middle': #Transport Layer
            MaterialDescriptors=[ECNL/EG, EG, Eps10, eMass, hMass,EdgeJDOS,ENegDiff]
        else: #Photolayer
            MaterialDescriptors=[ECNL/EG, EG, Eps10,excitonBinding,EdgeJDOS,ENegDiff]
        InitialTrainingDesc[i+len(goodLayer)]=MaterialDescriptors
    #Now get initial SVM attempt
    clfInitial = svm.SVC(kernel=SVM_Kernel,C=SVM_C,max_iter=SVMIterations)
    clfInitial.fit(InitialTrainingDesc,InitialTrainingClasses)
    #print np.array(Classification)
    scoresInitial = cross_validation.cross_val_score(clfInitial, InitialTrainingDesc, np.array(InitialTrainingClasses), cv=CrossValidationNum)    #print clf.support_vectors_
    print(clfInitial.score(InitialTrainingDesc,InitialTrainingClasses))
    print(scoresInitial)
    print("Accuracy: %0.2f (+/- %0.2f)" % (scoresInitial.mean(), scoresInitial.std() * 2)) 
    
    #Check if S4VM is desired then run
    if NewSVMPoints>0 and PointCombinations>0:
        #Initialize for loop over randomly chosen extra training points
        ExtraPoints=[[]]*PointCombinations #combinations of extra materials
        SVMOptimizing=[[]]*PointCombinations #Optimization function for each SVM fit
        
        IDsToChoose=[x for x in FilteredIDs if x not in goodLayer and x not in badLayer] #avoid choosing mateial already in training set
        for i in range(0,PointCombinations): #Here generate all combinations of extra training points to be used
            ExtraPoints[i]=random.sample(IDsToChoose,NewSVMPoints)
        #file for writing optimization data
        filenameOpt=directory+'Heterostructure'+LayerToStudy+'SVMOptimization.txt'
        fOpt=open(filenameOpt,'w')
        fOpt.write('#Trial Points'+'\t'+'Score'+'\t'+'-HingeLoss'+'\t'+'CrossValidation'+'\n')
    
        #begin main S4VM loop
        for i in range(0,PointCombinations):
            #print i
            ThisCombination=ExtraPoints[i] #choose the extra points to use
            ExtraPointsDescs=[[]]*NewSVMPoints #holds descriptors for new points
            for j in range(0,NewSVMPoints): #construct descriptor lists for extra points
                ExtraLoc=FilteredIDs.index(ThisCombination[j])
                ExtraPointsDescs[j]=MaterialDescriptorMatrix[ExtraLoc]
            #Now find categories with initial SVM    
            predictExtraInitial=list(clfInitial.predict(ExtraPointsDescs))
            #predictExtraInitial=list(np.random.choice([-1,1],NewSVMPoints)) #random assignment for testing, convergence issues
            #Now extend Matrix for descriptors and classification
            ExtendedTrainingDesc=InitialTrainingDesc+ExtraPointsDescs
            ExtendedTrainingClasses=InitialTrainingClasses+predictExtraInitial
            OldClasses=copy.copy(ExtendedTrainingClasses) #This will be updated each loop
            NewClasses=copy.copy(InitialTrainingClasses)+[0]*len(predictExtraInitial)
            #print OldClasses
            for S4VMLoops in range(0,MaxS4VM):
                #refit SVM using OldClasses
                clfLoop = svm.SVC(kernel=SVM_Kernel,C=SVM_C,max_iter=SVMIterations)
                clfLoop.fit(ExtendedTrainingDesc,OldClasses) #This fits SVM
                #print np.mean(cross_validation.cross_val_score(clfLoop, ExtendedTrainingDesc, np.array(OldClasses), cv=CrossValidationNum))
                #Now recategorize each extra point
                for j in range(0,NewSVMPoints):
                    NewClasses[j+len(InitialTrainingClasses)]=clfLoop.predict(ExtendedTrainingDesc[j+len(InitialTrainingClasses)])[0]
                #print NewClasses
                if np.allclose(OldClasses,NewClasses)==True: #no reassignment of classes
                    break
                else:
                    OldClasses=copy.copy(NewClasses)
            #print NewClasses
            #Now have to evaluate fitness function for converged SVM surface
            loss=float(HingeLoss(list(clfLoop.coef_[0]),clfLoop.intercept_,ExtendedTrainingDesc,NewClasses))
            cvPoint=cross_validation.cross_val_score(clfLoop, ExtendedTrainingDesc, np.array(NewClasses), cv=CrossValidationNum).mean()
            score=clfLoop.score(ExtendedTrainingDesc,NewClasses)
            Optimize=ThisCombination+[score,-loss,cvPoint,cvPoint/loss] #maximize (-loss or cv or cv/loss)
            SVMOptimizing[i]=Optimize
            #print Optimize
        #Write Optimization Matrix to file
        fOpt.writelines('\t'.join(str(j) for j in i) + '\n' for i in SVMOptimizing)
        fOpt.close()
        #Choose best SVM fit
        OptimizerValue=max(l[NewSVMPoints+S4VMChoice] for l in SVMOptimizing)
        #print OptimizerValue
        #for qqq in SVMOptimizing:
        #    print qqq
        BestSVMNum=int(np.where(np.isclose(SVMOptimizing,OptimizerValue,10**-8))[0]) #Combination of extra point leading to best SVM fit
        #print BestSVMNum
        #Now reevaluate to find best SVM surface
        ThisCombination=ExtraPoints[BestSVMNum] #choose the extra points to use
        ExtraPointsDescs=[[]]*NewSVMPoints #holds descriptors for new points
        for j in range(0,NewSVMPoints): #construct descriptor lists for extra points
            ExtraLoc=FilteredIDs.index(ThisCombination[j])
            ExtraPointsDescs[j]=MaterialDescriptorMatrix[ExtraLoc]
        #Now find categories with initial SVM    
        predictExtraInitial=list(clfInitial.predict(ExtraPointsDescs))
        #predictExtraInitial=list(np.random.choice([-1,1],NewSVMPoints)) #random assignment for testing
        #Now extend Matrix for descriptors and classification
        ExtendedTrainingDesc=InitialTrainingDesc+ExtraPointsDescs
        ExtendedTrainingClasses=InitialTrainingClasses+predictExtraInitial
        OldClasses=copy.copy(ExtendedTrainingClasses) #This will be updated each loop
        NewClasses=copy.copy(InitialTrainingClasses)+[0]*len(predictExtraInitial)
        #print OldClasses
        for S4VMLoops in range(0,MaxS4VM):
            #refit SVM using OldClasses
            clfInitial = svm.SVC(kernel=SVM_Kernel,C=SVM_C,max_iter=SVMIterations)
            clfInitial.fit(ExtendedTrainingDesc,OldClasses) #This fits SVM
            #print np.mean(cross_validation.cross_val_score(clfLoop, ExtendedTrainingDesc, np.array(OldClasses), cv=CrossValidationNum))
            #Now recategorize each extra point
            for j in range(0,NewSVMPoints):
                NewClasses[j+len(InitialTrainingClasses)]=clfInitial.predict(ExtendedTrainingDesc[j+len(InitialTrainingClasses)])[0]
            #print NewClasses
            if np.allclose(OldClasses,NewClasses)==True: #no reassignment of classes
                break
            else:
                OldClasses=copy.copy(NewClasses)
        #print NewClasses
        scoresFinal = cross_validation.cross_val_score(clfInitial, ExtendedTrainingDesc, np.array(NewClasses), cv=CrossValidationNum)    #print clf.support_vectors_
        print(clfInitial.score(ExtendedTrainingDesc,NewClasses))
        print(scoresFinal)
        #print clfInitial.coef_
        print("Accuracy: %0.2f (+/- %0.2f)" % (scoresFinal.mean(), scoresFinal.std() * 2)) 
    
    #Finished with either SVM or S4VM   
    filename=directory+'Heterostructure'+LayerToStudy+'SVM.txt'
    f=open(filename,'w')
    f.write('#MP_Number'+'\t'+'CNL'+'\t'+'EG'+'\t'+'EFermi'+'\t'+'ValenceMax'+'\t'+'CondMin'+'\t'+'ENegDiff'+'\t'+'Formula'+'\t'+'Cost'+'Good?'+'\n')
    for i in range(0,len(np.atleast_1d(LayersData))):
        materialID=np.atleast_1d(LayersData)[i][0]
        materialIndex=IDList.index(materialID)
        electronicIndex=ElectronicIDList.index(materialID)
        ECNL=ElectronicData[electronicIndex][1]
        EG=ElectronicData[electronicIndex][2]
        Eps10=OpticalData[materialIndex][1]
        eMass=OpticalData[materialIndex][2]
        hMass=OpticalData[materialIndex][3]
        excitonBinding=OpticalData[materialIndex][4]
        EdgeJDOS=OpticalData[materialIndex][5]
        ENegDiff=ENegDiffs[materialIndex]
        if Descriptors[materialIndex][10]=='True':
            direct=1.0 #direct band gap
        else:
            direct=-1.0 #inderect band gap
        if LayerToStudy!='Middle':
            MaterialDescriptorsCheck=[ECNL/EG, EG, Eps10, eMass, hMass,EdgeJDOS,ENegDiff]
        else:
            MaterialDescriptorsCheck=[ECNL/EG, EG, Eps10,excitonBinding,EdgeJDOS,ENegDiff]
        
        group=clfInitial.predict(MaterialDescriptorsCheck)
        DataToWrite=list(np.atleast_1d(LayersData)[i])
        if group==1 or materialID in goodLayer:
            for j in DataToWrite:
                f.write(str(j)+'\t')
            f.write('\n')
    f.close()    
      
    return directory+'Heterostructure'+LayerToStudy+'SVM.txt' #file name with SVM approved materials


def ConstructHeterostructures(ValidMatFiles):
    CNLDataLeft=np.atleast_1d(np.genfromtxt(ValidMatFiles[0],dtype=None))
    PossibleMiddlesAll=np.atleast_1d(np.genfromtxt(ValidMatFiles[1],dtype=None))
    CNLDataRight=np.atleast_1d(np.genfromtxt(ValidMatFiles[2],dtype=None))
    
    filename0=directory+'AllPossibleHeterostructures_AllFilters_LinCorr.txt'
    f0=open(filename0,'w')
    f0.write('#LMPID'+'\t'+'CMPID'+'\t'+'RMPID'+'\t'+'LName'+'\t'+'CName'+'\t'+'RName'+'\t'+'LGap'+'\t'+'CGap'+'\t'+'RGap'+'\t'+'EDiff1'+'\t'+'EDiff2'+'\t'+'EDiff3'+'\t'+'EDiff4'+'\t'+'CVBM'+'\t'+'Cost'+'\n')
    
    for i in range(len(PossibleMiddlesAll)):    
        PossibleLefts=[]
        PossibleRights=[]
        ReferenceVBM=PossibleMiddlesAll[i][4]
        ReferenceCBM=PossibleMiddlesAll[i][5]
        for j in range(len(CNLDataLeft)): #first check if suitable for left
            if LeftOffsets[3]<=CNLDataLeft[j][4]-ReferenceVBM<=LeftOffsets[2] and LeftOffsets[1]<=CNLDataLeft[j][5]-ReferenceCBM<=LeftOffsets[0]:
                PossibleLefts.append(j)
                #print CNLData[j][0][2]
        for j in range(len(CNLDataRight)):
            #now to the right
            if RightOffsets[3]<=CNLDataRight[j][4]-ReferenceVBM<=RightOffsets[2] and RightOffsets[1]<=CNLDataRight[j][5]-ReferenceCBM<=RightOffsets[0]:
                PossibleRights.append(j)
                #print CNLData[j][0][2]
        structures=list(itertools.product(PossibleLefts,[PossibleMiddlesAll[i][0]],PossibleRights)) #All possible structures
        #now get data to write to file
        CName=PossibleMiddlesAll[i][7].decode('utf-8')
        CGap=PossibleMiddlesAll[i][2]
        CMPID=PossibleMiddlesAll[i][0]
        CCost=PossibleMiddlesAll[i][8]
        if len(structures)>0:
            #filename=directory+'/PossibleHeterostructuresCurtaroloCorrectedCNL0_AllFilters_'+CName+'.txt'
            #f=open(filename,'w')
            #f.write('#LMPID'+'\t'+'CMPID'+'\t'+'RMPID'+'\t'+'LName'+'\t'+'CName'+'\t'+'RName'+'\t'+'LGap'+'\t'+'CGap'+'\t'+'RGap'+'\t'+'EDiff1'+'\t'+'EDiff2'+'\t'+'EDiff3'+'\t'+'EDiff4'+'\t'+'CVBM'+'\t'+'Cost'+'\n') 
            for j in range(0,len(structures)):
                LMPID=CNLDataLeft[structures[j][0]][0]
                RMPID=CNLDataRight[structures[j][2]][0]
                LName=CNLDataLeft[structures[j][0]][7].decode('utf-8')
                RName=CNLDataRight[structures[j][2]][7].decode('utf-8')
                LGap=CNLDataLeft[structures[j][0]][2]
                RGap=CNLDataRight[structures[j][2]][2]
                EDiff1=CNLDataLeft[structures[j][0]][5]-ReferenceCBM
                EDiff2=CNLDataLeft[structures[j][0]][4]-ReferenceVBM
                EDiff3=CNLDataRight[structures[j][2]][5]-ReferenceCBM
                EDiff4=CNLDataRight[structures[j][2]][4]-ReferenceVBM
                Cost=CNLDataLeft[structures[j][0]][8]+CNLDataRight[structures[j][2]][8]+CCost
                #f.write(str(int(LMPID))+'\t'+str(int(CMPID))+'\t'+str(int(RMPID))+'\t'+LName+'\t'+CName+'\t'+RName+'\t'+str(LGap)+'\t'+str(CGap)+'\t'+str(RGap)+'\t'+str(EDiff1)+'\t'+str(EDiff2)+'\t'+str(EDiff3)+'\t'+str(EDiff4)+'\t'+str(ReferenceVBM)+'\t'+str(Cost)+'\n')
                f0.write(str(int(LMPID))+'\t'+str(int(CMPID))+'\t'+str(int(RMPID))+'\t'+LName+'\t'+CName+'\t'+RName+'\t'+str(LGap)+'\t'+str(CGap)+'\t'+str(RGap)+'\t'+str(EDiff1)+'\t'+str(EDiff2)+'\t'+str(EDiff3)+'\t'+str(EDiff4)+'\t'+str(ReferenceVBM)+'\t'+str(Cost)+'\n')
            #f.close()
    f0.close()
    
    return filename0


def CountStructures(StructFile):
    HeterostructureData=np.genfromtxt(StructFile,dtype=None)
    print('Number of Structures = ' + str(len(HeterostructureData)))
    Compositions=np.genfromtxt('ChemComps.txt',dtype=None)
    CompIDs=[]
    for i in range(0,len(Compositions)):
        CompIDs.append(Compositions[i][0])

    LeftIDs=[]
    MiddleIDs=[]
    RightIDs=[]
    for i in range(0,len(HeterostructureData)):
        LeftIDs.append(HeterostructureData[i][0])
        MiddleIDs.append(HeterostructureData[i][1])
        RightIDs.append(HeterostructureData[i][2])
    
    LeftCount=collections.Counter(LeftIDs)
    LeftNums=sorted(list(set(LeftIDs)))
    
    MidCount=collections.Counter(MiddleIDs)
    MidNums=sorted(list(set(MiddleIDs)))
    
    RightCount=collections.Counter(RightIDs)
    RightNums=sorted(list(set(RightIDs)))
    
    filename1=directory+'11LeftFrequencies.txt'
    filename2=directory+'11MiddleFrequencies.txt'
    filename3=directory+'11RightFrequencies.txt'
    fl=open(filename1,'w')
    fm=open(filename2,'w')
    fr=open(filename3,'w')
    fl.write('#Formula'+'\t'+'MPID'+'\t'+'Frequency'+'\n')
    fm.write('#Formula'+'\t'+'MPID'+'\t'+'Frequency'+'\n')
    fr.write('#Formula'+'\t'+'MPID'+'\t'+'Frequency'+'\n')
    
    for i in LeftNums:
        MatIndex=CompIDs.index(i)
        MatName=Compositions[MatIndex][1]
        Frequency=LeftCount[i]
        fl.write(MatName+'\t'+str(i)+'\t'+str(Frequency)+'\n')
    for i in MidNums:
        MatIndex=CompIDs.index(i)
        MatName=Compositions[MatIndex][1]
        Frequency=MidCount[i]
        fm.write(MatName+'\t'+str(i)+'\t'+str(Frequency)+'\n')
    for i in RightNums:
        MatIndex=CompIDs.index(i)
        MatName=Compositions[MatIndex][1]
        Frequency=RightCount[i]
        fr.write(MatName+'\t'+str(i)+'\t'+str(Frequency)+'\n')
    fl.close()
    fm.close()
    fr.close()    
    return


AllData=np.genfromtxt('CNData_DensityEHullNAt_CompENeg_GapCorrCNL0.txt',dtype=None) #This includes the gap correction
OpticalData=np.genfromtxt('OpticalProperties.txt',dtype=None)
OpticIDs=[]
for i in range(0,len(OpticalData)):
    OpticIDs.append(OpticalData[i][0])
ElectronicIDs=[]
for i in range(0,len(AllData)):
    ElectronicIDs.append(AllData[i][0])

ChoosePhotolayers(Lefts, Middles, Rights, LeftMinGap, LeftMaxGap, PhotoMinGap, PhotoMaxGap, RightMinGap, RightMaxGap, LeftRequireDirect, RequireDirect, RightRequireDirect)

for iterloop in range(0,iterations):
    print(iterloop)
    directory=topDirectory+'Iteration'+str(iterloop)+'/' #where output files will be written
    if not os.path.exists(directory): #make directory
        os.makedirs(directory)
    AssembleFiles=[] #list of material file to assemble structures.  Order: LMR
    for layerPos in AllLayers: #loop over all layer positions
        if layerPos in Layers: #Layer to perform SVM
            trainingFileG=directory+'SVMTraining'+'Iteration'+str(iterloop)+'Good'+layerPos+'.txt' #good training data
            trainingFileB=directory+'SVMTraining'+'Iteration'+str(iterloop)+'Bad'+layerPos+'.txt' #bad training data
            fG=open(trainingFileG,'w')
            fB=open(trainingFileB,'w')
            if layerPos=='Left':
                for j in LeftTrainingInitialGood:
                    fG.write(str(j)+'\n')
                for j in LeftTrainingInitialBad:
                    fB.write(str(j)+'\n')
            elif layerPos=='Middle':
                for j in MiddleTrainingInitialGood:
                    fG.write(str(j)+'\n')
                for j in MiddleTrainingInitialBad:
                    fB.write(str(j)+'\n')
            elif layerPos=='Right':
                for j in RightTrainingInitialGood:
                    fG.write(str(j)+'\n')
                for j in RightTrainingInitialBad:
                    fB.write(str(j)+'\n')
            fB.close()
            fG.close()
            AssembleFiles.append(SVMMaterial(iterloop,layerPos))
        else: #layer not to perform SVM
            copyfile(topDirectory+'Heterostructure'+layerPos+'.txt',directory+'Heterostructure'+layerPos+'.txt')
            AssembleFiles.append(directory+'Heterostructure'+layerPos+'.txt')

    #Now combine approved materials into heterostructure
    structuresFile=ConstructHeterostructures(AssembleFiles)

    #Count each layer
    CountStructures(structuresFile)

    #find most common layers for SVM
    for qq in AllLayers:
        if qq in Layers: #Layers to SVM
            Frequencies=np.atleast_1d(np.array(np.genfromtxt(directory+'11'+qq+'Frequencies.txt',dtype=None)))
            Frequencies = sorted(Frequencies, key=lambda Frequencies_entry: Frequencies_entry[2], reverse=True)
            totalMaterials=len(Frequencies)
            numAdd=int(math.ceil(SVMAppendFrac*totalMaterials))
            for rr in range(0,numAdd):
                if qq=='Left' and 'Left' in Layers:
                    LeftTrainingInitialGood.append(Frequencies[rr][1])
                elif qq=='Right' and 'Right' in Layers:
                    RightTrainingInitialGood.append(Frequencies[rr][1])
                elif qq=='Middle' and 'Middle' in Layers:
                    MiddleTrainingInitialGood.append(Frequencies[rr][1])
    
    LeftTrainingInitialGood=list(set(LeftTrainingInitialGood))
    MiddleTrainingInitialGood=list(set(MiddleTrainingInitialGood))
    RightTrainingInitialGood=list(set(RightTrainingInitialGood))
    
    LeftTrainingInitialBad=LeftTrainingInitialBad+RightTrainingInitialGood
    RightTrainingInitialBad=RightTrainingInitialBad+LeftTrainingInitialGood
    
    #for each side make sure no material is both good and bad
    LeftConflicts=list(set(LeftTrainingInitialGood) & set(LeftTrainingInitialBad))
    if LeftConflicts:
        for LCons in LeftConflicts:
            LeftTrainingInitialGood.remove(LCons)
            LeftTrainingInitialBad.remove(LCons)
    RightConflicts=list(set(RightTrainingInitialGood) & set(RightTrainingInitialBad))
    if RightConflicts:
        for RCons in RightConflicts:
            RightTrainingInitialGood.remove(RCons)
            RightTrainingInitialBad.remove(RCons)
print('Done')

<ipython-input-13-056716c40a4d>:454: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  AllData=np.genfromtxt('CNData_DensityEHullNAt_CompENeg_GapCorrCNL0.txt',dtype=None) #This includes the gap correction


0


<ipython-input-13-056716c40a4d>:346: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  CNLDataLeft=np.atleast_1d(np.genfromtxt(ValidMatFiles[0],dtype=None))
<ipython-input-13-056716c40a4d>:347: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  PossibleMiddlesAll=np.atleast_1d(np.genfromtxt(ValidMatFiles[1],dtype=None))
<ipython-input-13-056716c40a4d>:348: VisibleDeprecationWarning: Reading unicode strings without specifying the encoding argument is deprecated. Set the encoding, use None for the system default.
  CNLDataRight=np.atleast_1d(np.genfromtxt(ValidMatFiles[2],dtype=None))


NameError: name 'LeftOffsets' is not defined

The following cell is the function used to rank structures

In [ ]:
def Resistance(ETLe,Ae,Ah,HTLh):
    return((ETLe+0.5*Ae+0.5*Ah+HTLh)**(-1))

The final cell below sorts by the figure of merit.

In [14]:
iteration=0
file=topDirectory+'Iteration'+str(iteration)+'/AllPossibleHeterostructures_AllFilters_LinCorr.txt'
Structures=np.genfromtxt(file,dtype=None)
#print(Structures)

OpticalData=np.genfromtxt('OpticalProperties.txt',dtype=None)
OpticIDs=[]
for i in range(0,len(OpticalData)):
    OpticIDs.append(OpticalData[i][0])
#print(OpticIDs)

OutFile=topDirectory+'Iteration'+str(iteration)+'/Structs.txt'
f=open(OutFile,'w')
#f.write('#LMPID'+'\t'+'CMPID'+'\t'+'RMPID'+'\t'+'LName'+'\t'+'CName'+'\t'+'RName'+'\t'+'LGap'+'\t'+'CGap'+'\t'+'RGap'+'\t'+'EDiff1'+'\t'+'EDiff2'+'\t'+'EDiff3'+'\t'+'EDiff4'+'\t'+'CVBM'+'\t'+'Cost'+'\t'+'ETLeMass'+'\t'+'ActiveeMass'+'\t'+'ActivehMass'+'\t'+'HTLhMass'+'\t'+'Resistive'+'\n')

for i in range(0,len(Structures)):
    Mat0=Structures[i][0] #left, ETL
    Mat1=Structures[i][1] # active layer
    Mat2=Structures[i][2] #right, HTL
    
    Mat0Loc=OpticIDs.index(Mat0)
    Mat1Loc=OpticIDs.index(Mat1)
    Mat2Loc=OpticIDs.index(Mat2)

    ETLeMass=OpticalData[Mat0Loc][2]
    ActiveeMass=OpticalData[Mat1Loc][2]
    ActivehMass=OpticalData[Mat1Loc][3]
    HTLhMass=OpticalData[Mat2Loc][3]
    
    #Write data to new file
    for item in Structures[i]:
        f.write(str(item)+'\t')
    for item in [ETLeMass,ActiveeMass,ActivehMass,HTLhMass]:
        f.write(str(item)+'\t')
    f.write(str(Resistance(ETLeMass,ActiveeMass,ActivehMass,HTLhMass))+'\n')
f.close()

#Sort file
os.system('sort -k20nr '+ OutFile +'> '+topDirectory+'Iteration'+str(iteration)+'/SortedStructures.txt')
print('Done')

<ipython-input-14-1529a774dc41>:3: UserWarning: genfromtxt: Empty input file: "Heterostructures_CdSe-1NoSVM/Iteration0/AllPossibleHeterostructures_AllFilters_LinCorr.txt"
  Structures=np.genfromtxt(file,dtype=None)


Done
